<a href="https://colab.research.google.com/github/Chinchilla7/AutoML-examples/blob/main/autoML/autoML.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Install Pacakges

In [1]:
!pip install tpot mljar-supervised

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [12]:
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from supervised.automl import AutoML


# Options Available

- mode — the package ships with four built-in models. 
  - The Explain mode is ideal for explaining and understanding the data. It results in visualizations of feature importance as well as tree visualizations.
  - The Perform is used when building ML models for production. 
  - The Compete is meant to build models used in machine learning competitions. 
  - The Optuna mode is used to search for highly-tuned ML models.
- algorithms — specifies the algorithms you would like to use. They are usually passed in as a list.
- results_path — the path where the results will be stored
- total_time_limit — the total time in seconds for training the model
- train_ensemble — dictates if an ensemble will be created at the end of the training process
- stack_models — determines if a models stack will be created
- eval_metric — the metric that will be optimized. If auto the logloss is used for classification problems while the rmse is used for regression problems

In [ ]:
#automl = AutoML(
    # mode="Explain"
    # algorithms=""
    # results_path="AutoML_22",
    # total_time_limit=30 * 60,
    # train_ensemble=True,
    # stack_models="",
    # eval_metric=""
#)

# Healthcare Dataset - SPARCS

## Load in dataset

In [2]:
import pandas as pd
sparcs = pd.read_csv('https://raw.githubusercontent.com/hantswilliams/HHA-507-2022/main/autoML/datasets/data_sparcs.csv')
sparcs

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2  Payment Typology 3  \
0      Private Health Insurance                       NaN                 NaN   
1        Blue Cross/Blue Shield                  Self-Pay            Self-Pay   
2                      Self-Pay                  Self-Pay            Self-Pay   
3                      Medicare                  Medicare            Self-Pay   
4        Blue Cross/Blue Shield  

In [3]:
sparcs.columns

Index(['Health Service Area', 'Hospital County',
       'Operating Certificate Number', 'Facility Id', 'Facility Name',
       'Age Group', 'Zip Code - 3 digits', 'Gender', 'Race', 'Ethnicity',
       'Length of Stay', 'Type of Admission', 'Patient Disposition',
       'Discharge Year', 'CCS Diagnosis Code', 'CCS Diagnosis Description',
       'CCS Procedure Code', 'CCS Procedure Description', 'APR DRG Code',
       'APR DRG Description', 'APR MDC Code', 'APR MDC Description',
       'APR Severity of Illness Code', 'APR Severity of Illness Description',
       'APR Risk of Mortality', 'APR Medical Surgical Description',
       'Payment Typology 1', 'Payment Typology 2', 'Payment Typology 3',
       'Birth Weight', 'Abortion Edit Indicator',
       'Emergency Department Indicator', 'Total Charges', 'Total Costs'],
      dtype='object')

## Potential variables of interest

- APR Risk of Mortality (categorical) 
- Total costs (continuous) 
- Length of Stay
-Total charges (continuous)
-Type of Admission (categorical)


In [4]:
sparcs['Total Charges'].describe()

count    2.358300e+04
mean     4.344052e+04
std      8.434949e+04
min      1.000000e+00
25%      1.226175e+04
50%      2.375403e+04
75%      4.702837e+04
max      4.410671e+06
Name: Total Charges, dtype: float64

In [5]:
sparcs['Type of Admission'].value_counts()

Emergency        14968
Elective          4508
Newborn           2285
Urgent            1743
Trauma              63
Not Available       16
Name: Type of Admission, dtype: int64

In [6]:
sparcs['Gender'].value_counts()

F    13187
M    10395
U        1
Name: Gender, dtype: int64

### **Create new model**

In [7]:
X = sparcs.drop(columns=['Type of Admission'])

In [8]:
y = sparcs["Type of Admission"]

In [9]:
X

Health Service Area Hospital County  Operating Certificate Number  \
0              Western NY        Allegany                      226700.0   
1              Western NY        Allegany                      228000.0   
2              Western NY        Allegany                      228000.0   
3              Western NY        Allegany                      228000.0   
4              Western NY        Allegany                      228000.0   
...                   ...             ...                           ...   
23578         Long Island         Suffolk                     5157003.0   
23579         Long Island         Suffolk                     5157003.0   
23580         Long Island         Suffolk                     5157003.0   
23581         Long Island         Suffolk                     5157003.0   
23582         Long Island         Suffolk                     5157003.0   

       Facility Id                                      Facility Name  \
0             37.0                         Cuba Memorial Hospital Inc   
1             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
2             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
3             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
4             39.0  Memorial Hosp of Wm F & Gertrude F Jones A/K/A...   
...            ...                                                ...   
23578        943.0                     St Catherine of Siena Hospital   
23579        943.0                     St Catherine of Siena Hospital   
23580        943.0                     St Catherine of Siena Hospital   
23581        943.0                     St Catherine of Siena Hospital   
23582        943.0                     St Catherine of Siena Hospital   

         Age Group Zip Code - 3 digits Gender        Race          Ethnicity  \
0         30 to 49                 147      M       White  Not Span/Hispanic   
1         18 to 29                 148      F       White  Not Span/Hispanic   
2          0 to 17                 147      M       White  Not Span/Hispanic   
3      70 or Older                 148      F       White  Not Span/Hispanic   
4         50 to 69                 148      M       White  Not Span/Hispanic   
...            ...                 ...    ...         ...                ...   
23578  70 or Older                 117      F       White  Not Span/Hispanic   
23579      0 to 17                 117      F  Other Race   Spanish/Hispanic   
23580     30 to 49                 117      M       White  Not Span/Hispanic   
23581  70 or Older                 117      M       White  Not Span/Hispanic   
23582  70 or Older                 117      F       White  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
0      ...                 Minor                          Medical   
1      ...                 Minor                          Medical   
2      ...                 Minor                          Medical   
3      ...              Moderate                          Medical   
4      ...                 Major                          Medical   
...    ...                   ...                              ...   
23578  ...              Moderate                          Medical   
23579  ...                 Minor                          Medical   
23580  ...                 Minor                          Medical   
23581  ...                 Major                          Medical   
23582  ...                 Major                          Medical   

             Payment Typology 1        Payment Typology 2 Payment Typology 3  \
0      Private Health Insurance                       NaN                NaN   
1        Blue Cross/Blue Shield                  Self-Pay           Self-Pay   
2                      Self-Pay                  Self-Pay           Self-Pay   
3                      Medicare                  Medicare           Self-Pay   
4        Blue Cross/Blue Shield       

In [10]:
y

0           Urgent
1           Urgent
2          Newborn
3        Emergency
4        Emergency
           ...    
23578    Emergency
23579      Newborn
23580       Urgent
23581    Emergency
23582    Emergency
Name: Type of Admission, Length: 23583, dtype: object

In [13]:
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, test_size=0.25)

In [16]:
X_test

Health Service Area Hospital County  Operating Certificate Number  \
10276       New York City           Bronx                     7000008.0   
6774      Capital/Adirond          Warren                     5601000.0   
14200       New York City       Manhattan                     7002002.0   
18400       New York City          Queens                     7003004.0   
296            Western NY            Erie                     1401014.0   
...                   ...             ...                           ...   
2725         Finger Lakes          Monroe                     2701005.0   
9614        New York City           Bronx                     7000006.0   
22037         Long Island          Nassau                     2952006.0   
19149       New York City          Queens                     7003010.0   
12072       New York City           Kings                     7001019.0   

       Facility Id                                 Facility Name    Age Group  \
10276       1172.0        Lincoln Medical & Mental Health Center     50 to 69   
6774        1005.0                          Glens Falls Hospital     30 to 49   
14200       1439.0                       Mount Sinai Beth Israel     50 to 69   
18400       1630.0             Long Island Jewish Medical Center  70 or Older   
296          207.0                Buffalo General Medical Center  70 or Older   
...            ...                                           ...          ...   
2725         413.0                      Strong Memorial Hospital     50 to 69   
9614        1168.0  Montefiore Medical Center-Wakefield Hospital     50 to 69   
22037        551.0                           St. Joseph Hospital  70 or Older   
19149       1637.0                   NewYork-Presbyterian/Queens  70 or Older   
12072       1304.0                   NYU Lutheran Medical Center      0 to 17   

      Zip Code - 3 digits Gender                    Race          Ethnicity  \
10276                 104      M  Black/African American  Not Span/Hispanic   
6774                  128      F                   White  Not Span/Hispanic   
14200                 112      M  Black/African American   Spanish/Hispanic   
18400                 113      F                   White  Not Span/Hispanic   
296                   143      M                   White  Not Span/Hispanic   
...                   ...    ...                     ...                ...   
2725                  146      M  Black/African American  Not Span/Hispanic   
9614                  104      M  Black/African American  Not Span/Hispanic   
22037                 117      M                   White  Not Span/Hispanic   
19149                 113      F                   White  Not Span/Hispanic   
12072                 112      F  Black/African American  Not Span/Hispanic   

       ... APR Risk of Mortality APR Medical Surgical Description  \
10276  ...              Moderate                          Medical   
6774   ...                 Minor                         Surgical   
14200  ...                 Minor                          Medical   
18400  ...              Moderate                         Surgical   
296    ...              Moderate                          Medical   
...    ...                   ...                              ...   
2725   ...                 Major                          Medical   
9614   ...                 Minor                          Medical   
22037  ...                 Major                          Medical   
19149  ...                 Major                          Medical   
12072  ...                 Minor                          Medical   

             Payment Typology 1      Payment Typology 2  \
10276                  Medicaid                Medicaid   
6774     Blue Cross/Blue Shield                     NaN   
14200                  Medicaid                Self-Pay   
18400                  Medicare                Medicaid   
296                    Medicare  Blue Cross/Blue Shield   


In [14]:
automl = AutoML(results_path="sparcs_classification", mode="Explain")

In [15]:
automl.fit(X_train, y_train)

Linear algorithm was disabled.
AutoML directory: sparcs_classification
The task is multiclass_classification with evaluation metric logloss
AutoML will use algorithms: ['Baseline', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 2 models
1_Baseline logloss 1.047051 trained in 0.71 seconds


2_DecisionTree logloss 0.376179 trained in 26.96 seconds
* Step default_algorithms will try to check up to 3 models
3_Default_Xgboost logloss 0.221934 trained in 60.95 seconds
4_Default_NeuralNetwork logloss 0.359239 trained in 8.78 seconds
5_Default_RandomForest logloss 0.343617 trained in 31.48 seconds
* Step ensemble will try to check up to 1 model
Ensemble logloss 0.221934 trained in 0.6 seconds
AutoML fit time: 139.93 seconds
AutoML best model: 3_Default_Xgboost


AutoML(results_path='sparcs_classification')

In [17]:
pred = automl.predict(X_test)
pred

array(['Emergency', 'Elective', 'Urgent', ..., 'Emergency', 'Emergency',
       'Elective'], dtype=object)

In [18]:
automl.report()

## Regression 

In [19]:
import numpy as np
import pandas as pd
from supervised.automl import AutoML

df = pd.read_csv("https://raw.githubusercontent.com/hantswilliams/HHA-507-2022/main/autoML/datasets/data_regression_housing.csv")
x_cols = [c for c in df.columns if c != "AGE"]
X = df[x_cols]
y = df["AGE"]

In [20]:
df

CRIM    ZN  INDUS  CHAS    NOX     RM   AGE     DIS  RAD  TAX  \
0    0.00632  18.0   2.31     0  0.538  6.575  65.2  4.0900    1  296   
1    0.02731   0.0   7.07     0  0.469  6.421  78.9  4.9671    2  242   
2    0.02729   0.0   7.07     0  0.469  7.185  61.1  4.9671    2  242   
3    0.03237   0.0   2.18     0  0.458  6.998  45.8  6.0622    3  222   
4    0.06905   0.0   2.18     0    NaN  7.147  54.2  6.0622    3  222   
..       ...   ...    ...   ...    ...    ...   ...     ...  ...  ...   
501  0.06263   0.0  11.93     0  0.573  6.593  69.1  2.4786    1  273   
502  0.04527   0.0  11.93     0  0.573  6.120  76.7  2.2875    1  273   
503  0.06076   0.0  11.93     0  0.573  6.976  91.0  2.1675    1  273   
504  0.10959   0.0  11.93     0  0.573  6.794  89.3  2.3889    1  273   
505  0.04741   0.0  11.93     0  0.573  6.030  80.8  2.5050    1  273   

     PTRATIO       B  LSTAT  MEDV  
0       15.3  396.90   4.98  24.0  
1       17.8  396.90   9.14  21.6  
2       17.8  392.83   4.03  34.7  
3       18.7  394.63   2.94  33.4  
4       18.7  396.90   5.33  36.2  
..       ...     ...    ...   ...  
501     21.0  391.99   9.67  22.4  
502     21.0  396.90   9.08  20.6  
503     21.0  396.90   5.64  23.9  
504     21.0  393.45   6.48  22.0  
505     21.0  396.90   7.88  11.9  

[506 rows x 14 columns]

In [21]:
x_cols

['CRIM',
 'ZN',
 'INDUS',
 'CHAS',
 'NOX',
 'RM',
 'DIS',
 'RAD',
 'TAX',
 'PTRATIO',
 'B',
 'LSTAT',
 'MEDV']

In [22]:
X

CRIM    ZN  INDUS  CHAS    NOX     RM     DIS  RAD  TAX  PTRATIO  \
0    0.00632  18.0   2.31     0  0.538  6.575  4.0900    1  296     15.3   
1    0.02731   0.0   7.07     0  0.469  6.421  4.9671    2  242     17.8   
2    0.02729   0.0   7.07     0  0.469  7.185  4.9671    2  242     17.8   
3    0.03237   0.0   2.18     0  0.458  6.998  6.0622    3  222     18.7   
4    0.06905   0.0   2.18     0    NaN  7.147  6.0622    3  222     18.7   
..       ...   ...    ...   ...    ...    ...     ...  ...  ...      ...   
501  0.06263   0.0  11.93     0  0.573  6.593  2.4786    1  273     21.0   
502  0.04527   0.0  11.93     0  0.573  6.120  2.2875    1  273     21.0   
503  0.06076   0.0  11.93     0  0.573  6.976  2.1675    1  273     21.0   
504  0.10959   0.0  11.93     0  0.573  6.794  2.3889    1  273     21.0   
505  0.04741   0.0  11.93     0  0.573  6.030  2.5050    1  273     21.0   

          B  LSTAT  MEDV  
0    396.90   4.98  24.0  
1    396.90   9.14  21.6  
2    392.83   4.03  34.7  
3    394.63   2.94  33.4  
4    396.90   5.33  36.2  
..      ...    ...   ...  
501  391.99   9.67  22.4  
502  396.90   9.08  20.6  
503  396.90   5.64  23.9  
504  393.45   6.48  22.0  
505  396.90   7.88  11.9  

[506 rows x 13 columns]

In [23]:
y

0      65.2
1      78.9
2      61.1
3      45.8
4      54.2
       ... 
501    69.1
502    76.7
503    91.0
504    89.3
505    80.8
Name: AGE, Length: 506, dtype: float64

In [24]:
automl = AutoML(results_path="sparcs_regression", mode="Explain")
automl.fit(X, y)

AutoML directory: sparcs_regression
The task is regression with evaluation metric rmse
AutoML will use algorithms: ['Baseline', 'Linear', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will ensemble available models
AutoML steps: ['simple_algorithms', 'default_algorithms', 'ensemble']
* Step simple_algorithms will try to check up to 3 models
1_Baseline rmse 30.026682 trained in 1.74 seconds
2_DecisionTree rmse 15.428887 trained in 4.2 seconds
3_Linear rmse 17.141279 trained in 2.73 seconds
* Step default_algorithms will try to check up to 3 models
4_Default_Xgboost rmse 13.683388 trained in 5.63 seconds
5_Default_NeuralNetwork rmse 12.830056 trained in 0.84 seconds
6_Default_RandomForest rmse 14.250642 trained in 7.33 seconds
* Step ensemble will try to check up to 1 model
Ensemble rmse 12.704008 trained in 0.3 seconds
AutoML fit time: 30.63 seconds
AutoML best model: Ensemble


AutoML(results_path='sparcs_regression')

In [25]:
df["predictions"] = automl.predict(X)


In [26]:
print("Predictions")
print(df[["AGE", "predictions"]].head())

Predictions
    AGE  predictions
0  65.2    63.169380
1  78.9    52.861020
2  61.1    41.372815
3  45.8    27.006589
4  54.2    42.278704


# Download outputs

In [27]:
# get current working directory
import os
os.getcwd()

'/content'

In [28]:
folders = os.listdir()
foldersML = [x for x in folders if x.startswith('sparcs')]
print(foldersML)

['sparcs_regression', 'sparcs_classification']


In [33]:
!zip -r /content/sparcs.zip /content/sparcs_classification

  adding: content/sparcs_classification/ (stored 0%)
  adding: content/sparcs_classification/README.md (deflated 68%)
  adding: content/sparcs_classification/params.json (deflated 62%)
  adding: content/sparcs_classification/ldb_performance.png (deflated 25%)
  adding: content/sparcs_classification/progress.json (deflated 92%)
  adding: content/sparcs_classification/split_validation_indices.npy (deflated 66%)
  adding: content/sparcs_classification/Ensemble/ (stored 0%)
  adding: content/sparcs_classification/Ensemble/README.md (deflated 75%)
  adding: content/sparcs_classification/Ensemble/roc_curve.png (deflated 9%)
  adding: content/sparcs_classification/Ensemble/status.txt (stored 0%)
  adding: content/sparcs_classification/Ensemble/learning_curves.png (deflated 10%)
  adding: content/sparcs_classification/Ensemble/predictions_ensemble.csv (deflated 60%)
  adding: content/sparcs_classification/Ensemble/confusion_matrix_normalized.png (deflated 11%)
  adding: content/sparcs_classifi

In [34]:
!zip -r /content/sparcs.zip /content/sparcs_regression


  adding: content/sparcs_regression/ (stored 0%)
  adding: content/sparcs_regression/README.md (deflated 69%)
  adding: content/sparcs_regression/params.json (deflated 63%)
  adding: content/sparcs_regression/ldb_performance.png (deflated 25%)
  adding: content/sparcs_regression/progress.json (deflated 90%)
  adding: content/sparcs_regression/split_validation_indices.npy (deflated 69%)
  adding: content/sparcs_regression/Ensemble/ (stored 0%)
  adding: content/sparcs_regression/Ensemble/README.md (deflated 51%)
  adding: content/sparcs_regression/Ensemble/status.txt (stored 0%)
  adding: content/sparcs_regression/Ensemble/learning_curves.png (deflated 12%)
  adding: content/sparcs_regression/Ensemble/predicted_vs_residuals.png (deflated 12%)
  adding: content/sparcs_regression/Ensemble/predictions_ensemble.csv (deflated 48%)
  adding: content/sparcs_regression/Ensemble/true_vs_predicted.png (deflated 11%)
  adding: content/sparcs_regression/Ensemble/ensemble.json (deflated 50%)
  addin